In [1]:
import pandas as pd
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from bs4 import BeautifulSoup
import time
import sqlalchemy
from sqlalchemy import create_engine


In [2]:
# login
def login(driver, instahandle, instapassword):
    username = driver.find_element(By.CSS_SELECTOR, "input[name='username']")
    password = driver.find_element(By.CSS_SELECTOR, "input[name='password']")
    username.clear()
    password.clear()
    username.send_keys(instahandle)
    password.send_keys(instapassword)
    driver.find_element(By.CSS_SELECTOR, "button[type='submit']").click()
    time.sleep(5)
    return True

In [3]:
def skip_login_info(driver):
    #save your login info?
    time.sleep(10)
    notnow = driver.find_element("xpath", "//button[contains(text(), 'Not Now')]").click()
def turn_off_notif(driver):
    #turn on notif
    time.sleep(10)
    notnow2 = driver.find_element("xpath", "//button[contains(text(), 'Not Now')]").click()

In [4]:
#searchbox
def search(driver, instapage):
    time.sleep(5)
    searchbox = driver.find_element(By.CSS_SELECTOR, "input[placeholder='Search']")
    searchbox.clear()
    searchbox.send_keys(instapage)
    time.sleep(5)
    #selects the item
    searchbox.send_keys(Keys.ENTER);
    time.sleep(5)
    #clicks enter
    searchbox.send_keys(Keys.ENTER)

In [5]:
def set_window_size(driver):
    time.sleep(5)
    a=driver.get_window_size()
    driver.set_window_size(a["width"], a["height"])

In [6]:
def scroller(driver):
    #scroll
    time.sleep(5)
    scrolldown = driver.execute_script(
    "window.scrollTo(0, document.body.scrollHeight);var scrolldown=document.body.scrollHeight;return scrolldown;")
    match = False
    timeout = 0
    while not match:
        last_count = scrolldown
        time.sleep(3)
        scrolldown = driver.execute_script(
        "window.scrollTo(0, document.body.scrollHeight);var scrolldown=document.body.scrollHeight;return scrolldown;")
        if last_count == scrolldown:
            match = True
        if timeout == 0:
            break
        else:
            timeout-=1


In [7]:
def insta_posts(driver, limit=10):
    posts = []
    links = driver.find_elements(By.TAG_NAME, 'a')
    for link in links[:limit]:
        post = link.get_attribute('href')
        if '/p/' in post:
            posts.append(post)
    return posts

In [8]:
def getdata(driver,posts, page="",):
    raw_data = []
    for post in posts:
        print(f"Visiting page {post}")
        driver.get(post)
        time.sleep(5)
        shortcode = driver.current_url.split("/")[-2]
        print("shortcode", shortcode)
        selector = "div._aa06"
        try:
            if driver.find_element(By.CSS_SELECTOR, selector) is not None:
                content = driver.find_elements(By.CSS_SELECTOR, selector)
                for con in content:
                    html = con.get_attribute('innerHTML')
                    with open('dummy_sec.html', 'w',encoding="utf-8") as f:
                        f.write(html)
                    soup = BeautifulSoup(html,  'html.parser')

                    for link in soup.find_all('a'):
                        raw_data.append({
                            'tag':link.text,
                            'link':link.attrs.get('href'),
                            'page':soup.find('a').attrs.get('href'),
                            'date':soup.find('time').attrs.get('datetime'),
                            'img':soup.find('img').attrs.get('src')
                        })
                    print(raw_data)
            else:
                print(f"{selector} not found")
        except Exception as e:
            print(e)
        finally:
            time.sleep(5)
    return raw_data


In [9]:
def covert_data_to_df(raw_data):
    df = pd.DataFrame(raw_data)
    df[df['tag'].str.startswith('#')]
    return df
from sqlalchemy import create_engine


#     engine = create_engine('sqlite://db.sqlite', echo=False)
#     df.to_sql('hashtags', con=engine)
    # df.to_sql()
    # conn = sqlite3.connect('test_database')
    # c = conn.cursor()
    # c.execute('CREATE TABLE IF NOT EXISTS hastags(tag,link,page,date)')
    # conn.commit()
    # df.to_sql('hashtags', conn, if_exists='replace', index = False)

In [10]:
def convert_df_to_csv(df):
    df.to_csv('hastags_rawdata1.csv', index=None)
    print('Process Completed')

**Calling functions**

In [11]:
#installing driver
mdriver = webdriver.Chrome(ChromeDriverManager().install())
mdriver.get("https://www.instagram.com/")
time.sleep(2)
insta_handle='twilightqueenbee1579'
insta_password='!$@%67'
insta_page='random_shotsbyme'
#if login successful
try:
    if login(mdriver,insta_handle,insta_password):
        print("Login successful")
        skip_login_info(mdriver)
        turn_off_notif(mdriver)
        mdriver.get("https://www.instagram.com/explore")
        set_window_size(mdriver)
        scroller(mdriver)
        time.sleep(3)
        fetched_posts=insta_posts(mdriver, 10)
        print(fetched_posts)
        print(f'len of posts {len(fetched_posts)}')
        fetched_data=getdata(mdriver,fetched_posts,insta_page)
        dataframe=covert_data_to_df(fetched_data)
        convert_df_to_csv(dataframe)
    else:
        print("Wrong credentials")
except Exception as e:
     print(e)

# mdriver.quit()



[WDM] - Downloading: 100%|██████████| 6.79M/6.79M [00:00<00:00, 9.45MB/s]
C:\Users\Ananya Misra\AppData\Local\Temp\ipykernel_13236\4146343365.py:2: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  mdriver = webdriver.Chrome(ChromeDriverManager().install())


Login successful
['https://www.instagram.com/p/CnCSKxuoQ4v/', 'https://www.instagram.com/p/CnPD2OftKxW/', 'https://www.instagram.com/p/CnOj1Zbq0bc/', 'https://www.instagram.com/p/CnCmEBvSHFS/', 'https://www.instagram.com/p/Cm_p7ybSGVm/', 'https://www.instagram.com/p/CnMedOaKIm_/', 'https://www.instagram.com/p/CnOG09xLjCf/', 'https://www.instagram.com/p/CnNBtBvv2ke/', 'https://www.instagram.com/p/CnLhGGeLtru/', 'https://www.instagram.com/p/CnHViHiqSne/']
len of posts 10
Visiting page https://www.instagram.com/p/CnCSKxuoQ4v/
shortcode CnCSKxuoQ4v
'NoneType' object has no attribute 'attrs'
Visiting page https://www.instagram.com/p/CnPD2OftKxW/
shortcode CnPD2OftKxW
[]
[]
[{'tag': 'instantbollywood', 'link': '/instantbollywood/', 'page': '/instantbollywood/', 'date': '2023-01-10T12:52:04.000Z', 'img': 'https://instagram.flko6-1.fna.fbcdn.net/v/t51.2885-19/299955958_104691272316346_6128863586793629494_n.jpg?stp=dst-jpg_s150x150&_nc_ht=instagram.flko6-1.fna.fbcdn.net&_nc_cat=1&_nc_ohc=7GeVk1

In [12]:
dataframe

tag                                 link  \
0     instantbollywood                   /instantbollywood/   
1     @alwaysramcharan                    /alwaysramcharan/   
2              @iamsrk                             /iamsrk/   
3                                          /the_realdinesh/   
4       the_realdinesh                     /the_realdinesh/   
..                 ...                                  ...   
359  v_e_n_k_a_t_pandu                  /v_e_n_k_a_t_pandu/   
360                 6d  /p/CnHViHiqSne/c/17980599271882428/   
361                                        /kalyankaramala/   
362     kalyankaramala                     /kalyankaramala/   
363                10h  /p/CnHViHiqSne/c/17934735749609687/   

                    page                      date  \
0     /instantbollywood/  2023-01-10T12:52:04.000Z   
1     /instantbollywood/  2023-01-10T12:52:04.000Z   
2     /instantbollywood/  2023-01-10T12:52:04.000Z   
3       /the_realdinesh/  2023-01-10T13:07:03.000Z   
4       /the_realdinesh/  2023-01-10T13:07:03.000Z   
..                   ...                       ...   
359  /v_e_n_k_a_t_pandu/  2023-01-09T03:58:03.000Z   
360  /v_e_n_k_a_t_pandu/  2023-01-09T03:58:03.000Z   
361     /kalyankaramala/  2023-01-15T08:37:41.000Z   
362     /kalyankaramala/  2023-01-15T08:37:41.000Z   
363     /kalyankaramala/  2023-01-15T08:37:41.000Z   

                                                   img  
0    https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
1    https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
2    https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
3    https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
4    https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
..                                                 ...  
359  https://scontent.cdninstagram.com/v/t51.2885-1...  
360  https://scontent.cdninstagram.com/v/t51.2885-1...  
361  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
362  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
363  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  

[364 rows x 5 columns]

In [13]:
dataframe.img[0]

'https://instagram.flko6-1.fna.fbcdn.net/v/t51.2885-19/299955958_104691272316346_6128863586793629494_n.jpg?stp=dst-jpg_s150x150&_nc_ht=instagram.flko6-1.fna.fbcdn.net&_nc_cat=1&_nc_ohc=7GeVk1zMIqwAX9EhGbS&edm=APU89FABAAAA&ccb=7-5&oh=00_AfCK7rnxDX-pC1Lvze2yFLhtXHd1FAxvy0zIvlza0eqb7w&oe=63C8AC05&_nc_sid=86f79a'

In [21]:
#filtering the dataframe on the basis of #
mask = dataframe['tag'].str.contains('#', case=False, na=False)
new_dataframe=dataframe[mask]
#converting the new dataframe to csv
# new_dataframe
sorted_df=new_dataframe.sort_values('tag')
sorted_df

tag                                               link  \
47        #Pathaan❤️❤️  /explore/tags/pathaan%E2%9D%A4%EF%B8%8F%E2%9D%...   
315          #anupamaa                            /explore/tags/anupamaa/   
236  #beautifulactress                    /explore/tags/beautifulactress/   
241    #beautifulgirls                      /explore/tags/beautifulgirls/   
113  #bestversionofyou                    /explore/tags/bestversionofyou/   
..                 ...                                                ...   
237          #trending                            /explore/tags/trending/   
227     #trendingaudio                       /explore/tags/trendingaudio/   
239         #viralpost                           /explore/tags/viralpost/   
238        #viralreels                          /explore/tags/viralreels/   
305     #youngtigerntr                       /explore/tags/youngtigerntr/   

                           page                      date  \
47              /smartynaaz710/  2023-01-10T13:36:47.000Z   
315               /bhanubeats_/  2023-01-07T12:53:15.000Z   
236  /celebraty_official_page_/  2023-01-09T03:53:11.000Z   
241  /celebraty_official_page_/  2023-01-09T03:53:11.000Z   
113              /success_volt/  2023-01-04T13:17:02.000Z   
..                          ...                       ...   
237  /celebraty_official_page_/  2023-01-09T03:53:11.000Z   
227  /celebraty_official_page_/  2023-01-09T03:53:11.000Z   
239  /celebraty_official_page_/  2023-01-09T03:53:11.000Z   
238  /celebraty_official_page_/  2023-01-09T03:53:11.000Z   
305               /bhanubeats_/  2023-01-07T12:53:15.000Z   

                                                   img  
47   https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
315  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
236  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
241  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
113  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
..                                                 ...  
237  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
227  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
239  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
238  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
305  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  

[71 rows x 5 columns]

tag  \
47              #Pathaan❤️❤️   
50                #farahkhan   
99              #lifelessons   
100          #selflovequotes   
101                  #habits   
..                       ...   
314              #sidsriramn   
315                #anupamaa   
316           #telugumusic❣️   
317  #pspk💕💕💕😎💕💕💕😍😍😍💕💕💕💕😘💕💕💕   
318        #telugulovelyrics   

                                                  link             page  \
47   /explore/tags/pathaan%E2%9D%A4%EF%B8%8F%E2%9D%...  /smartynaaz710/   
50                            /explore/tags/farahkhan/   /viralbhayani/   
99                          /explore/tags/lifelessons/   /success_volt/   
100                      /explore/tags/selflovequotes/   /success_volt/   
101                              /explore/tags/habits/   /success_volt/   
..                                                 ...              ...   
314                          /explore/tags/sidsriramn/    /bhanubeats_/   
315                            /explore/tags/anupamaa/    /bhanubeats_/   
316       /explore/tags/telugumusic%E2%9D%A3%EF%B8%8F/    /bhanubeats_/   
317  /explore/tags/pspk%F0%9F%92%95%F0%9F%92%95%F0%...    /bhanubeats_/   
318                    /explore/tags/telugulovelyrics/    /bhanubeats_/   

                         date  \
47   2023-01-10T13:36:47.000Z   
50   2023-01-10T08:12:20.000Z   
99   2023-01-04T13:17:02.000Z   
100  2023-01-04T13:17:02.000Z   
101  2023-01-04T13:17:02.000Z   
..                        ...   
314  2023-01-07T12:53:15.000Z   
315  2023-01-07T12:53:15.000Z   
316  2023-01-07T12:53:15.000Z   
317  2023-01-07T12:53:15.000Z   
318  2023-01-07T12:53:15.000Z   

                                                   img  
47   https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
50   https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
99   https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
100  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
101  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
..                                                 ...  
314  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
315  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
316  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
317  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  
318  https://instagram.flko6-1.fna.fbcdn.net/v/t51....  

[71 rows x 5 columns]

In [15]:
convert_df_to_csv(sorted_df)

Process Completed


In [16]:
def save_dataframe(df:pd.DataFrame):
    from datetime import datetime
    val = datetime.now().strftime("_%d_%m_%y")
    engine = create_engine('sqlite:///hashtags.sqlite3', echo=False)
    df.to_sql(f'hashtag_{val}', con=engine, if_exists='append')



In [17]:
# datetime.now()
save_dataframe(new_dataframe)

*this command is not running: python3 -m venv env
red line in line 94*

In [18]:
from datetime import datetime
value = datetime.now().strftime("_%d_%m_%y")
print(value)

_16_01_23
